# Domain generation

In [1]:
import time

from eminus import Atoms, read_xyz, SCF
from eminus.domains import domain_cuboid, domain_isovalue, domain_sphere, truncate
from eminus.energies import get_Esic, get_n_single
from eminus.extras import view_atoms
from eminus.orbitals import KSO

In [2]:
# Start by creating an `Atoms` object for lithium hydride
# Use a small `s` to make the resulting grid not too dense to display it
atoms = Atoms(*read_xyz('LiH.xyz'), ecut=3, center=True)
scf = SCF(atoms)
scf.run();

XYZ file comment: "Experimental geometry from CCCBDB: https://cccbdb.nist.gov/exp2x.asp?casno=7580678&charge=0"
Start auto minimization...
Method  Iteration  Etot [Eh]    dEtot [Eh]   |Gradient|   
pccg           1   +2.714422    
pccg           2   +0.361635    +2.3528e+00  [+2.81e+03]  
pccg           3   -2.131111    +2.4927e+00  [+5.20e+01]  
pccg           4   -3.863223    +1.7321e+00  [+1.04e+01]  
pccg           5   -4.498148    +6.3492e-01  [+2.11e+00]  
pccg           6   -4.749755    +2.5161e-01  [+6.75e-01]  
pccg           7   -4.837534    +8.7779e-02  [+1.53e-01]  
pccg           8   -4.880686    +4.3151e-02  [+5.39e-02]  
pccg           9   -4.900844    +2.0158e-02  [+2.28e-02]  
pccg          10   -4.908952    +8.1080e-03  [+8.96e-03]  
pccg          11   -4.911921    +2.9685e-03  [+3.95e-03]  
pccg          12   -4.912719    +7.9836e-04  [+1.10e-03]  
pccg          13   -4.912947    +2.2790e-04  [+2.95e-04]  
pccg          14   -4.913014    +6.6873e-05  [+9.31e-05]  
pc

In [3]:
# Create a boolean mask for a cuboidal domain
# This will create a domain with side lengths of 3 Bohr,
# with the center in the center at the center of mass of our molecule
mask = domain_cuboid(atoms, 3)

# Display the domain along with the atom positions
# The `view_atoms` function can be used outside of notebooks
view_atoms(atoms, atoms._r[mask])

In [4]:
# The same can be done for a spherical domain with a radius of 3 Bohr
mask = domain_sphere(atoms, 3)
view_atoms(atoms, atoms._r[mask])

In [5]:
# One can also define more than one center
# This will create multiple domains and merge them, here shown with the atom positions as centers
mask = domain_sphere(atoms, 3, atoms.X)
view_atoms(atoms, atoms._r[mask])

In [6]:
# An isovalue can be used to generate a domain from a real-space field data like the density
mask = domain_isovalue(scf.n, 1e-3)
view_atoms(atoms, atoms._r[mask])

# The same can be done for orbitals
psi = KSO(scf)
# mask = domain_isovalue(psi[0, :, 0], 1e-2)
# view_atoms(atoms, atoms._r[mask])

In [7]:
# Compare to the density volume plot
view_atoms(scf, plot_n=True, percent=95)

In [8]:
# Truncated densities can be used to calculate, e.g., SIC energies
# Calculate the single-electron densities from Kohn-Sham orbitals first
ni = get_n_single(atoms, atoms.J(psi))

In [9]:
# Calculate the SIC energy for untruncated densities
start = time.perf_counter()
esic = get_Esic(scf, scf.W, ni)
end = time.perf_counter()
print(f'Esic(untruncated) = {esic:.9f} Eh\nTime(untruncated) =  {end - start:.6f} s')

# Calculate the SIC energy for truncated densities
# One can notice a small energy deviation, but a faster calculation time
mask = domain_isovalue(ni, 1e-4)
ni_trunc = truncate(ni, mask)
start = time.perf_counter()
esic_trunc = get_Esic(scf, scf.W, ni_trunc)
end = time.perf_counter()
print(f'Esic( truncated ) = {esic_trunc:.9f} Eh\nTime( truncated ) =  {end - start:.6f} s')

Esic(untruncated) = -0.202926117 Eh
Time(untruncated) =  0.104138 s
Esic( truncated ) = -0.204063872 Eh
Time( truncated ) =  0.009115 s


In [10]:
# The truncated SIC energy will converge for smaller isovalues to the untruncated value
mask = domain_isovalue(ni, 0)
ni_trunc = truncate(ni, mask)
esic_trunc = get_Esic(scf, scf.W, ni_trunc)
print(esic == esic_trunc)

True
